Feed it all the research papers and blog posts I've looked at

Be able to ask questions like "what is the last paper I read about X?" and recommend papers

Imagine if recall for browser history/literature was like recalling memories; based on semantics instead of keywords

lol would be nice to have this for this project:

research papers/links

[OpenAI cookbook example of using nonpublic data for Q&A](https://github.com/openai/openai-cookbook/blob/main/examples/Question_answering_using_embeddings.ipynb?ref=mattboegner.com)

[Retrieval augmented NLP](https://arxiv.org/pdf/2005.11401.pdf)

In [2]:
!pip install openai

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.6/73.6 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 30.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 33.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.6/149.6 kB 20.7 MB/s eta 0:00:00


In [ ]:
import openai
openai.api_key = input()

In [4]:
def get_query(question: str):

  query = f"""
  Write many keywords that I can use to query for answers to for the following question: {question}. The embedding database contains webscraped data. Do not include anything in your response other than the expansion words.
  """

  completion = openai.ChatCompletion.create(
    model="gpt-3.5-turbo",
    temperature=0.1,
    messages=[
          {"role": "system", "content": "You write semantic search queries to embedding database"},
          {"role": "user", "content": query},
      ]
  )
  return completion.choices[0].message.content

In [5]:
question = "What is that paper I read about LLMs and their ability camus?"
query = get_query(question)
query

'- LLMs\n- Camus\n- Paper\n- Read\n- Ability\n- Webscraped\n- Data\n- Query\n- Semantic search\n- Embedding database'

In [10]:
!pip install sentence_transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 9.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 78.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 88.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 32.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 126.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 66.5 MB/s eta 0:00:00
  Created wheel for sentence_transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125926 sha256=164014d4f8b6f36b0bde1e03434ce65de7a7b85e8f7fcd1e557549bfc155c589
  Stored in directory: /root/.cache/pip/wheels/62/f2/10/1e606fd5f02395388f74e7462910fe851042f97238cbbd902f
Successfully built sentence_transformers


In [7]:
!pip install InstructorEmbedding

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
# get the response and use it to query Pinecone vector db

from sentence_transformers import SentenceTransformer
import torch

device = 'cuda' if torch.cuda.is_available() else 'cpu'
if device != 'cuda':
    print(f"You are using {device}. This is much slower than using "
          "a CUDA-enabled GPU. If on Colab you can change this by "
          "clicking Runtime > Change runtime type > GPU.")

from InstructorEmbedding import INSTRUCTOR
model = INSTRUCTOR('hkunlp/instructor-base', device=device)
# model = SentenceTransformer('all-MiniLM-L6-v2', device=device)
model

In [12]:
instruction = "Represent the user query: "
# query_emb = model.encode(query)
query_emb = model.encode([[instruction, query]])
query_emb.shape

(1, 768)

In [13]:
_id = '0'
metadata = {'text': query}

vectors = [(_id, query_emb, metadata)]

In [14]:
!pip3 install pinecone-client

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.1/179.1 kB 14.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.0/60.0 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 283.7/283.7 kB 31.7 MB/s eta 0:00:00


In [73]:
import os
import pinecone

# get api key from app.pinecone.io
PINECONE_API_KEY = input()
PINECONE_ENV = "asia-southeast1-gcp-free"

pinecone.init(
    api_key=PINECONE_API_KEY,
    environment=PINECONE_ENV
)

In [74]:
index_name = 'imessage'

# only create index if it doesn't exist
if index_name not in pinecone.list_indexes():
    pinecone.create_index(
        name=index_name,
        dimension=model.get_sentence_embedding_dimension(),
        metric='cosine'
    )

# now connect to the index
index = pinecone.Index(index_name)

In [75]:
index.query(
  vector=model.encode("google").tolist(),
  top_k=1,
    include_metadata=True,
    namespace="uno"
)

{'matches': [{'id': '0ea52cd8e05147dc780433b478f858ea34c548760692e46460b16b599f89c56d',
              'metadata': {'text': 'alexandria will depeu arxiv - Google '
                                   'SearchGoogle×Please click here if you are '
                                   'not redirected within a few seconds.    '
                                   'AllNewsImagesVideos Maps Shopping Books '
                                   'Search tools    Any timeAny timePast '
                                   'hourPast 24 hoursPast weekPast monthPast '
                                   'yearAll resultsAll '
                                   'resultsVerbatimIncluding results for '
                                   'alexandria will depue arxivSearch only for '
                                   'alexandria will depeu arxivwill depue on '
                                   'Twitter: "Today, I\'m announcing '
                                   'Alexandria, an open ...twitter.com › '
         

In [76]:
def query(text, k):
    query_emb = model.encode(text)
    res = index.query(
        vector=model.encode([[instruction,text]]).tolist(),
        top_k=k,
        include_metadata=True,
        namespace="uno"
    )["matches"]
    return res

In [77]:
def qans(text, k):
    q = get_query(text)
    print(q)
    docs = query(q, k)
    print(docs)
    completion = openai.ChatCompletion.create(
        model="gpt-3.5-turbo",
        messages=[
            {
                "role": "system",
                "content": "You write semantic search queries to embedding database",
            },
            {"role": "user", "content": f"Here is your question '{text}' use the following texts to assist in answering it: \n {docs} \n Answer the question no matter what"},
            # {"role": "assistant", "content": "
            # {"role": "user", "content": "Where was it played?"}
        ],
    )
    return completion.choices[0].message.content


In [111]:
docs = index.query(
        vector=model.encode("").tolist(),
        top_k=1e4,
        include_values=True,
        include_metadata=True,
        namespace="uno"
    )["matches"]

In [79]:
docs[0]

{'id': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
 'metadata': {'text': '\n'
                      '\n'
                      'ERROR: The request could not be satisfied\n'
                      '\n'
                      '413 ERROR\n'
                      'The request could not be satisfied.\n'
                      '\n'
                      'Bad request.\n'
                      "We can't connect to the server for this app or website "
                      'at this time. There might be too much traffic or a '
                      'configuration error. Try again later, or contact the '
                      'app or website owner.\n'
                      '\n'
                      'If you provide content to customers through CloudFront, '
                      'you can find steps to troubleshoot and help prevent '
                      'this error by reviewing the CloudFront documentation.\n'
                      '\n'
                      '\n'
           

In [80]:
import numpy as np
v = []
ids = []
for i in docs:
    v.append(np.array(i["values"]))
    ids.append(i["id"])

In [81]:
nodes = []
for doc in docs:
    nodes.append({
          "id": doc["id"],
          "name": doc["metadata"]["title"],
          "val": doc["metadata"]["url"]
        })
links = []
CUTOFF = 1.1
for node_idx, node in enumerate(v):
    edges = []
    for edge_idx, edge in enumerate(v):
        if node_idx == edge_idx:
            pass
        if np.linalg.norm(node - edge) < CUTOFF:
            links.append({
                "source": ids[node_idx],
                "target": ids[edge_idx]
            })

In [82]:
links

[{'source': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
  'target': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054'},
 {'source': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
  'target': '28bacb8b68411b9d16906af58605647a993fe46a9be08e0bd1f197da46f5d8f2'},
 {'source': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
  'target': '9ef556ade7c1fd8daeb3cddd4f2bb7fa968a1d916706111a2c0f50433f939594'},
 {'source': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
  'target': 'bd1f99addcb1380e4f47fbf5066f708ec2d35350cc0c0e9f9c0620899bc5ccbd'},
 {'source': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
  'target': '144dc4ed2c278202d2c682535290d4f7b3472b0a4f3ed8310f886afcf5e1c9a7'},
 {'source': '6dee724d116a1ae6a54bc147dfb51a8800e88972c9d943968cddce5ca8094054',
  'target': '711f8d53f453839efca8ec9ddc957d642db038184a21b6e22c09991f91970c11'},
 {'source': '6dee724d116a1ae6a54bc

In [83]:
import json
with open("x_embeds.json", "w") as outfile:
    json.dump({
        "nodes":nodes,
        "links":links
    }, outfile)

In [84]:
qans("I'm writing a research paper on scaling laws in transformers?",3)

scaling laws, transformers, electrical engineering, power systems, energy efficiency, magnetic fields, electrical conductivity, voltage, current, power loss, core material, winding design, transformer design, transformer manufacturing, transformer testing, transformer maintenance, transformer operation, transformer protection, transformer reliability, transformer efficiency, transformer modeling, transformer simulation, transformer optimization, transformer performance, transformer analysis, transformer diagnostics, transformer monitoring, transformer fault detection, transformer fault diagnosis, transformer fault classification, transformer fault location, transformer fault identification, transformer fault tolerance, transformer fault prevention, transformer fault mitigation, transformer fault repair, transformer fault investigation, transformer safety, transformer standards, transformer regulations, transformer codes, transformer guidelines, transformer best practices, transformer i

'Scaling laws in transformers refer to the relationship between the size of a transformer and its performance, particularly in natural language processing tasks. Popular transformer models like BERT, GPT-3, and T5 have shown how scaling up the number of parameters can significantly improve their performance. However, there are also challenges in scaling transformers, such as increased computational requirements, longer training times, and potential overfitting. Recent research has explored alternative methods such as sparse attention mechanisms and log-precision transformers to mitigate these challenges.'

In [113]:
from sklearn.cluster import KMeans

data = np.array(v)
kmeans = KMeans(n_clusters=5) # TODO: auto find num clusters
kmeans.fit(data)
centroids = kmeans.cluster_centers_

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [114]:
centroid_list = []

for cluster_idx in range(kmeans.n_clusters):
    cluster_centroid = centroids[cluster_idx]
    centroid_list.append(cluster_centroid)
    # print(f"Cluster {cluster_idx+1}:")
    print("Centroid:", cluster_centroid)
    print('---')

Centroid: [-1.74024442e-02 -1.52387745e-02  2.62875498e-02  3.44883789e-02
 -9.71644927e-03 -2.94188519e-02 -6.14730524e-02  3.38017848e-02
 -7.89561596e-03 -8.25882272e-03  1.79151675e-02 -6.64609071e-02
  8.48635096e-02  3.28977140e-02  6.84356156e-02  3.45882820e-02
  1.37979189e-02 -2.80513094e-02  2.89393078e-02  2.87642827e-02
  2.45193870e-02 -2.90283470e-02 -4.40236074e-02  2.11677521e-02
 -2.77694504e-02  2.76116235e-02  3.36455980e-02 -4.09466077e-02
 -3.40444747e-02  1.98015805e-02  5.84158481e-02 -5.65567140e-03
 -4.53590633e-02  5.62765197e-02 -5.19765574e-02  1.73997080e-02
 -1.41985977e-02 -4.69252624e-02 -1.27281873e-02  2.71090021e-02
  1.08544257e-02 -7.78563289e-02 -1.87089188e-02  5.41015514e-02
 -5.57294681e-02 -2.15310401e-02  2.65352634e-02  4.71591932e-02
 -3.13387082e-02 -7.41488628e-02 -4.58039796e-02 -1.63382002e-02
 -3.53886882e-02 -2.81050965e-02 -1.69149114e-02 -9.55713785e-03
 -8.76092574e-03  1.73885255e-02  1.72719296e-02 -9.62264805e-04
 -5.60593289e-0

In [115]:
node.shape, cluster_centroid.shape

((768,), (768,))

In [116]:
# alexandria
PINECONE_API_KEY = input()
PINECONE_ENV = "us-central1-gcp"

pinecone.init(
    api_key=PINECONE_API_KEY,
    environment=PINECONE_ENV
)

In [117]:
index_name = "arxiv" # "https://the-arxiv-ef40355.svc.us-central1-gcp.pinecone.io/"
index = pinecone.Index(index_name)

if index_name not in pinecone.list_indexes():
  print("not here")

In [118]:
for index_name in pinecone.list_indexes():
  print(index_name)

arxiv


In [ ]:
centroid_list[0].tolist()

In [121]:
def get_similar(vector: list):

  rec_docs = index.query(
    vector=vector,
    top_k=3,
    include_metadata=True,
    namespace="v1"
  )

  return rec_docs['matches'][0]['id']

In [110]:
# for d in rec_docs['matches']:
#   print(d['id'])
#   print(d['metadata'])

# https://arxiv.org/abs/2210.02451

2210.02451
{'authors': ['Martínez-Ortí, Alberto', 'Adam, Sonia', 'Garippa, Giovanni', 'Boissier, Jérôme', 'Bargues, M Dolores', 'Mas-Coma, Santiago'], 'categories': ['q-bio.QM'], 'year': 2022.0}
2012.15073
{'authors': ['Park, Dayoon'], 'categories': ['math.NT'], 'year': 2020.0}
math/0604422
{'authors': ['Rajkovic, Predrag', 'Petkovic, Marko D.', 'Barry, Paul'], 'categories': ['math.CO', 'math.NT'], 'year': 2006.0}


In [122]:
for c in centroid_list:
  id = get_similar(c.tolist())
  print(id)

math/0604422
1201.4428
2005.03242
2004.13777
2210.02451


In [65]:
# better way to recommend most recent articles; query alexandria and check distance to nodes

arxiv_docs = index.query(
        vector=[0]*768,
        top_k=100,
        include_values=True,
        # include_metadata=True,
        namespace="v1"
    )

In [72]:
arxiv_docs

{'matches': [{'id': '2009.06272',
              'score': 0.0,
              'values': [0.0525411665,
                         -0.00960578,
                         0.0146067459,
                         -0.0537535846,
                         -0.0504603237,
                         -0.0449494831,
                         -0.102977276,
                         -0.00720129348,
                         -0.000838118838,
                         -0.0195892956,
                         0.0458781272,
                         0.0390602276,
                         -0.0231849123,
                         -0.0481137112,
                         -0.0279307421,
                         -0.0597233847,
                         0.00422804523,
                         -0.00541004259,
                         -0.00328768371,
                         -0.0118985604,
                         -0.0146550741,
                         -0.0225932524,
                         -0.0482189059,
                    

In [46]:
# index_stats_response = index.describe_index_stats()
# index_stats_response

{'dimension': 768,
 'index_fullness': 0.5,
 'namespaces': {'v1': {'vector_count': 2254198}},
 'total_vector_count': 2254198}